<a href="https://colab.research.google.com/gist/gyacynuk/2327d8fe847a71135971f2e0f591778d/copy-of-csc412-revnet.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
# Install Linux packages
!apt-get install fluidsynth

In [ ]:
# Install Python packages
!pip install pyfluidsynth
!pip install pypianoroll

In [3]:
import torch
from torch import nn
from torch.distributions import Normal
from torch.utils.data import Dataset, DataLoader, random_split, TensorDataset
from torch.optim.lr_scheduler import ReduceLROnPlateau
from torch.nn.utils import clip_grad_norm_
import torch.optim as optim
import numpy as np
from scipy.sparse import csc_matrix
import scipy.io.wavfile
import matplotlib.pyplot as plt
import pypianoroll as ppr
from IPython.display import Audio

In [ ]:
# Mount Google Drive filesystem
from google.colab import drive
drive.mount('/content/drive')

In [5]:
# Configure devices
cpu = torch.device('cpu') 
cuda = torch.device('cuda')

# Choose device for notebook (cpu or cuda)
device = cuda

In [13]:
def load_batched_dataset(file_pattern, num_files, reduce_dims=True,
                         batch_size=400, shuffle=True, bar_length=96,
                         pitch_range=128, verbose=True):
    """Load a dataset that has been batched across multiple files.
    
    Parameters
    ----------
    file_pattern: str
        The string pattern that the dataset files follow. For instance, if we
        wanted to load files ["data-0.npz", "data-1.npz"], then the pattern
        would be: "data-{}.npz".
    num_files: int
        The amount of files that should be loaded, using the provided pattern.
    reduce_dims: bool, optional
        Whether the dataset should have its dimensionality reduced by deleting
        pitch dimensions that are never played.
    batch_size: int, optional
        The batch size that should be used when building a DataLoader.
    shuffle: bool, optional
        The shuffle argument that should be used when building a DataLoader.
    bar_length: int, optional
        The length of a bar of music in absolute timestep representation.
    pitch_range: int, optional
        The range of pitches in the data representation.
    verbose: bool, optional
        When set to true, additional information and graphs will be produced.

    Returns
    -------
    dataset: torch.utils.data.Dataset
        The resulting dataset
    dataloader: torch.utils.data.DataLoader
        The resulting dataloader
    """
    def load_npz(path):
        """Helper function to load in a compressed numpy array"""
        with np.load(path) as f:
            data = np.zeros(f['shape'], np.bool_)
            data[[x for x in f['nonzero']]] = True
        return data

    def create_dataloader(paths, clip_pitch=None):
        """Helper function to create a dataloader from a list of .npz paths"""
        # Load each dataset from the provided paths
        datasets = []
        for path in paths:
            np_data = load_npz(path)
            binary_data = torch.from_numpy(np_data)
            scalar_data = torch.where(binary_data == True, 1.0, -1.0)
            datasets.append(scalar_data)
        dataset = torch.cat(datasets)

        # If clip_pitch argument was supplied, then clip the dataset's pitch
        if clip_pitch != None:
            min_pitch, max_pitch = clip_pitch
            piano_rolls = dataset.reshape(-1, bar_length, pitch_range)
            clipped_pitch_range = max_pitch - min_pitch + 1
            clipped_piano_rolls = piano_rolls[:,:,min_pitch:max_pitch+1]
            dataset = clipped_piano_rolls.reshape(-1, bar_length*clipped_pitch_range)

        # If verbose, then print dataset size
        if verbose:
            n = dataset.size()
            print('Successfully loaded dataset of size: {}'.format(n))

        # Create a TensorDataset and DataLoader
        ds = TensorDataset(dataset)
        dl = DataLoader(ds, batch_size=batch_size, shuffle=shuffle)
        return ds, dl

    # Compute paths and load dataset
    paths = [file_pattern.format(i) for i in range(num_files)]
    dataset, dataloader = create_dataloader(paths, None)

    # Compute a pitch histogram across the dataset, counting if a pitch occurs
    # over all bars (note: not the count of the pitch across all timesteps) 
    pitch_hist = torch.zeros(128)
    for i in range(len(dataset)):
        bar = dataset[i][0].reshape(96, 128)
        pitch_hist += torch.any(bar > 0, 0)

    # Calculate the indices of the min and max pitch
    indices = torch.arange(128) * torch.where(pitch_hist > 0, 1, 0)
    min_index = -1
    max_index = -1
    for ind in indices:
      if ind != 0:
        min_index = ind
        break
    for ind in torch.flip(indices, [0]):
      if ind != 0:
        max_index = ind
        break

    if verbose:
        # Print pitch band
        print('Non-zero pitch band: [{}, {}]'.format(min_index, max_index))

        # Plot pitch distribution
        fig, ax = plt.subplots(1, 2)
        fig.set_size_inches(24, 9)
        fig.suptitle('Dataset Pitch Distribution')
        ax[0].set_title('Pitch Occurrences by Bars')
        ax[0].bar(torch.arange(128), pitch_hist)
        ax[1].set_title('Is Pitch Present in Dataset')
        ax[1].plot(torch.arange(128), pitch_hist > 0)

    # If reduce_dims then recompute the dataset and dataloader, this time
    # clipping the pianorolls
    if reduce_dims:
        return create_dataloader(paths, [min_index, max_index])
    return dataset, dataloader

In [ ]:
# If dataset or dataloader was previously assigned, delete them to free memory
try:
    del dataset
    del dataloader
except Exception:
    pass

# Create a dataset and dataloader from our batched dataset
dataset, dataloader = load_batched_dataset(
    '/content/drive/MyDrive/CSC412/data/dataset-{}.npz',    # filepath pattern
    11)                                                     # number of batches

In [15]:
# Reference: Robin Bruegger, https://github.com/RobinBruegger/RevTorch

class ReversibleBlock(nn.Module):
    '''
    Elementary building block for building (partially) reversible architectures
    Implementation of the Reversible block described in the RevNet paper
    (https://arxiv.org/abs/1707.04585). Must be used inside a :class:`revtorch.ReversibleSequence`
    for autograd support.
    Arguments:
        f_block (nn.Module): arbitrary subnetwork whos output shape is equal to its input shape
        g_block (nn.Module): arbitrary subnetwork whos output shape is equal to its input shape
        split_along_dim (integer): dimension along which the tensor is split into the two parts requried for the reversible block
        fix_random_seed (boolean): Use the same random seed for the forward and backward pass if set to true 
    '''

    def __init__(self, f_block, g_block, split_along_dim=1, fix_random_seed = False):
        super(ReversibleBlock, self).__init__()
        self.f_block = f_block
        self.g_block = g_block
        self.split_along_dim = split_along_dim
        self.fix_random_seed = fix_random_seed
        self.random_seeds = {}

    def _init_seed(self, namespace):
        if self.fix_random_seed:
            self.random_seeds[namespace] = random.randint(0, sys.maxsize)
            self._set_seed(namespace)

    def _set_seed(self, namespace):
        if self.fix_random_seed:
            torch.manual_seed(self.random_seeds[namespace])

    def forward(self, x):
        """
        Performs the forward pass of the reversible block. Does not record any gradients.
        :param x: Input tensor. Must be splittable along dimension 1.
        :return: Output tensor of the same shape as the input tensor
        """
        x1, x2 = torch.chunk(x, 2, dim=self.split_along_dim)
        y1, y2 = None, None
        with torch.no_grad():
            self._init_seed('f')
            y1 = x1 + self.f_block(x2)
            self._init_seed('g')
            y2 = x2 + self.g_block(y1)

        return torch.cat([y1, y2], dim=self.split_along_dim)

    def backward_pass(self, y, dy, retain_graph):
        """
        Performs the backward pass of the reversible block.
        Calculates the derivatives of the block's parameters in f_block and g_block, as well as the inputs of the
        forward pass and its gradients.
        :param y: Outputs of the reversible block
        :param dy: Derivatives of the outputs
        :param retain_graph: Whether to retain the graph on intercepted backwards
        :return: A tuple of (block input, block input derivatives). The block inputs are the same shape as the block outptus.
        """
        
        # Split the arguments channel-wise
        y1, y2 = torch.chunk(y, 2, dim=self.split_along_dim)
        del y
        assert (not y1.requires_grad), "y1 must already be detached"
        assert (not y2.requires_grad), "y2 must already be detached"
        dy1, dy2 = torch.chunk(dy, 2, dim=self.split_along_dim)
        del dy
        assert (not dy1.requires_grad), "dy1 must not require grad"
        assert (not dy2.requires_grad), "dy2 must not require grad"

        # Enable autograd for y1 and y2. This ensures that PyTorch
        # keeps track of ops. that use y1 and y2 as inputs in a DAG
        y1.requires_grad = True
        y2.requires_grad = True

        # Ensures that PyTorch tracks the operations in a DAG
        with torch.enable_grad():
            self._set_seed('g')
            gy1 = self.g_block(y1)

            # Use autograd framework to differentiate the calculation. The
            # derivatives of the parameters of G are set as a side effect
            gy1.backward(dy2, retain_graph = retain_graph)

        with torch.no_grad():
            x2 = y2 - gy1 # Restore first input of forward()
            del y2, gy1

            # The gradient of x1 is the sum of the gradient of the output
            # y1 as well as the gradient that flows back through G
            # (The gradient that flows back through G is stored in y1.grad)
            dx1 = dy1 + y1.grad
            del dy1
            y1.grad = None

        with torch.enable_grad():
            x2.requires_grad = True
            self._set_seed('f')
            fx2 = self.f_block(x2)

            # Use autograd framework to differentiate the calculation. The
            # derivatives of the parameters of F are set as a side effec
            fx2.backward(dx1, retain_graph = retain_graph)

        with torch.no_grad():
            x1 = y1 - fx2 # Restore second input of forward()
            del y1, fx2

            # The gradient of x2 is the sum of the gradient of the output
            # y2 as well as the gradient that flows back through F
            # (The gradient that flows back through F is stored in x2.grad)
            dx2 = dy2 + x2.grad
            del dy2
            x2.grad = None

            # Undo the channelwise split
            x = torch.cat([x1, x2.detach()], dim=self.split_along_dim)
            dx = torch.cat([dx1, dx2], dim=self.split_along_dim)

        return x, dx

class _ReversibleModuleFunction(torch.autograd.function.Function):
    '''
    Integrates the reversible sequence into the autograd framework
    '''

    @staticmethod
    def forward(ctx, x, reversible_blocks, eagerly_discard_variables):
        '''
        Performs the forward pass of a reversible sequence within the autograd framework
        :param ctx: autograd context
        :param x: input tensor
        :param reversible_blocks: nn.Modulelist of reversible blocks
        :return: output tensor
        '''
        assert (isinstance(reversible_blocks, nn.ModuleList))
        for block in reversible_blocks:
            assert (isinstance(block, ReversibleBlock))
            x = block(x)
        ctx.y = x.detach() #not using ctx.save_for_backward(x) saves us memory by beeing able to free ctx.y earlier in the backward pass
        ctx.reversible_blocks = reversible_blocks
        ctx.eagerly_discard_variables = eagerly_discard_variables
        return x

    @staticmethod
    def backward(ctx, dy):
        '''
        Performs the backward pass of a reversible sequence within the autograd framework
        :param ctx: autograd context
        :param dy: derivatives of the outputs
        :return: derivatives of the inputs
        '''
        y = ctx.y
        if ctx.eagerly_discard_variables:
            del ctx.y
        for i in range(len(ctx.reversible_blocks) - 1, -1, -1):
            y, dy = ctx.reversible_blocks[i].backward_pass(y, dy, not ctx.eagerly_discard_variables)
        if ctx.eagerly_discard_variables:
            del ctx.reversible_blocks
        return dy, None, None

class ReversibleSequence(nn.Module):
    '''
    Basic building element for (partially) reversible networks
    A reversible sequence is a sequence of arbitrarly many reversible blocks. The entire sequence is reversible.
    The activations are only saved at the end of the sequence. Backpropagation leverages the reversible nature of
    the reversible sequece to save memory.
    Arguments:
        reversible_blocks (nn.ModuleList): A ModuleList that exclusivly contains instances of ReversibleBlock
        which are to be used in the reversible sequence.
        eagerly_discard_variables (bool): If set to true backward() discards the variables requried for 
		calculating the gradient and therefore saves memory. Disable if you call backward() multiple times.
    '''

    def __init__(self, reversible_blocks, eagerly_discard_variables = True):
        super(ReversibleSequence, self).__init__()
        assert (isinstance(reversible_blocks, nn.ModuleList))
        for block in reversible_blocks:
            assert(isinstance(block, ReversibleBlock))

        self.reversible_blocks = reversible_blocks
        self.eagerly_discard_variables = eagerly_discard_variables

    def forward(self, x):
        '''
        Forward pass of a reversible sequence
        :param x: Input tensor
        :return: Output tensor
        '''
        x = _ReversibleModuleFunction.apply(x, self.reversible_blocks, self.eagerly_discard_variables)
        return x

In [16]:
class FullyReversibleBlock(ReversibleBlock):
    """Extend ReversibleBlock implementing a reverse function"""

    def reverse(self, y):
        """Reverse the block forward operation, mapping an output tensor back to
        its original input.

        Parameters
        ----------
        y: torch.tensor
            An output tensor from the model.

        Returns
        -------
        x: torch.tensor
            The original input tensor that would have yielded y during the
            forward pass.
        """
        y1, y2 = torch.chunk(y, 2, dim=self.split_along_dim)
        x1, x2 = None, None
        with torch.no_grad():
            self._init_seed('g')
            x2 = y2 - self.g_block(y1)
            self._init_seed('f')
            x1 = y1 - self.f_block(x2)
        
        return torch.cat([x1, x2], dim=self.split_along_dim)

class FullyReversibleSequence(ReversibleSequence):
    """Extend FullyReversibleSequence implementing a reverse function"""

    def reverse(self, y):
        """Reverse the entire sequence, transforming a tensor from the model's
        latent space back to the dataspace.

        Parameters
        ----------
        y: torch.tensor
            A tensor from the model's latent space.

        Returns
        -------
        x: torch.tensor
            The dataspace tensor which corresponds to the given latent tensor y.
        """
        for block in self.reversible_blocks[::-1]:
            y = block.reverse(y)
        return y

In [ ]:
def saveModel(path, model):
  """Save a model in its entirety
  
  Parameters
  ----------
  path: str
    The path to the file where the model should be saved
  model: torch.nn.Module
    The model to be saved
  """
  torch.save(model, path)

In [ ]:
def loadModel(path, forInference=False):
  """Load a saved RevNet model

  Parameters
  ----------
  path: str
    The path to the file where the model should be read from
  forInference: bool, optional
    Whether the model should be loaded specifically for inference or not
  
  Returns
  -------
  model: torch.nn.Module
    The loaded model
  """
  model = torch.load(path)
  if forInference:
    model.eval()
  return model

In [17]:
def negative_log_loss(y, sigma=1.0):
    """Computes the negative log loss with respect to a fully factored Gaussian.

    Parameters
    ----------
    y: torch.tensor
        The model's output over a minibatch
    sigma: float, optional
        The standard deviation of the fully factored Gaussian used to compute
        the negative log loss. This value will be used to construct a diagonal
        covariance matrix.

    Returns
    -------
    nll: float
        The negative log loss of the minibatch, computed with a fully factored
        Gaussian with mean=0, and sd=sigma. This value is scaled to account for
        the batch size.
    """
    batch_size = y.size()[0]
    std_gaussian = Normal(0, sigma)
    nll = -torch.sum(std_gaussian.log_prob(y)) / batch_size
    return nll

In [18]:
def train(model, dataset, epochs=200, bs=256, lr=0.001, momentum=0.9,
          max_grad_norm=None, verbose=False):
    """Train a model to map training data to a fully factored Gaussian.

    Parameters
    ----------
    model: torch.nn.Module
        The model to be trained.
    dataset: torch.utils.data.Dataset
        The dataset to use as training data.
    epochs: int, optional
        The number of epochs to train the model for.
    bs: int, optional
        The batch size to use while training the model.
    lr: float, optional
        The learning rate to use while training.
    momentum: float, optional
        The momentum factor to use with SGD.
    max_grad_norm: float or None, optional
        The maximum gradient norm allowed before it will be clippped. If None
        then no gradient clipping will be done.
    verbose: boolean, optional
        Whether or not to output verbose updates during training. If True then
        loss will be reported after each epoch, and a graph of loss over
        training will be produced.
    
    Returns
    -------
    None
    """
    # Create a DataLoader from the supplied dataset
    dataloader = DataLoader(dataset, batch_size=bs, shuffle=True)

    # Configure the optimizer. We are using SGD with momentum, as we empirically
    # determined that this yields the best results (compared to vanilla SGD and
    # ADAM)
    optimizer = optim.SGD(model.parameters(), lr=lr, momentum=momentum)

    # Configure a scheduler to anneal the learning rate when the loss function
    # plateaus.
    scheduler = ReduceLROnPlateau(optimizer, 'min')

    # Keep track of loss over training so it can be plotted later.
    loss_over_training = []

    # Train the model
    for epoch in range(epochs):
        running_loss = 0.0
        for i, x in enumerate(dataloader):
            x = x[0]

            # Enable grad and send x to device
            x.requires_grad = True
            x = x.to(device)

            # zero the parameter gradients
            optimizer.zero_grad()

            # forward + backward + optimize
            y = model(x)
            loss = negative_log_loss(y)
            loss.backward()

            # Optionally clip gradient and step optimizer
            if max_grad_norm is not None:
                clip_grad_norm_(model.parameters(), max_grad_norm)
            optimizer.step()

            # print statistics
            running_loss += loss.item()

            # Clean up to avoid OOM error
            del x

        # Anneal LR
        scheduler.step(running_loss)

        # Print loss at end of epoch 
        if verbose or epoch == epochs - 1:
            print('[Epoch: %d] loss: %.3f' % (epoch + 1, running_loss * (bs / len(dataset))))
        loss_over_training.append(running_loss)
        running_loss = 0.0

    # If verbose is set to True, then plot the loss over training
    if verbose:
        fig, ax = plt.subplots(1, 1)
        fig.set_size_inches(16, 9)
        fig.suptitle('Loss Over Training')
        ax.set_xlabel('Epoch')
        ax.set_ylabel('Loss')
        ax.set_yscale('log')
        ax.plot(torch.arange(epochs)+1, torch.tensor(loss_over_training))

In [21]:
def generate_revnet(D, num_blocks, num_layers, activation=nn.Tanh,
                    final_activation=nn.Tanh, bias=True, final_bias=True):
    """A convenience function to generate a FullyReversibleSequence.
    
    Parameters
    ----------
    D: int
        The input/output dimension of each subnet f, g that composes a
        FullyReversibleBlock. This should be exactly half of the entire model's
        input dimension.
    num_blocks: int
        The number of blocks that will be stacked to form the
        FullyReversibleSequence.
    num_layers: int
        The number of layers that each subnet f, g will have. These will be
        fully-connected linear layers.
    activation: function, optional
        A function used to instantiate an activation function layer. This
        activation layer will be used in inbetween fully connected layers of
        each subnet f, g. Furthermore, this will be used for all blocks except
        the final block.
    final_activation: function, optional
        A function used to instantiate an activation function layer. This will
        be used in inbetween fully connected layers of each subnet f, g in the
        final block of the FullyReversibleSequence.
    bias: boolean, optional
        True if a bias term should be used on the fully connected layers of
        subnets f, g, in all blocks of the FullyReversibleSequence except for
        the last.
    final_bias: boolean, optional
        True if a bias term should be used on the fully connected layers of
        subnets f, g, in the final block of the the FullyReversibleSequence.

    Returns
    -------
    revnet: FullyReversibleSequence
        A RevNet implemented using the FullyReversibleSequence class, configured
        according to the given parameters.
    """

    def generate_subnet(bias, activation):
        """Helper function to generate subnets f, g."""
        first_layer = [nn.Linear(D,D, bias=bias).to(device)]
        rest_layers = [[activation(),nn.BatchNorm1d(D).to(device),nn.Linear(D,D,bias=bias).to(device)]
                       for _ in range(num_layers-1)]
        return nn.Sequential(*first_layer + [v for pair in rest_layers for v in pair])

    # Configure the first num_blocks-1 blocks of the network
    blocks = []
    for i in range(num_blocks-1):
        f = generate_subnet(bias, activation)
        g = generate_subnet(bias, activation)
        blocks.append(FullyReversibleBlock(f, g))

    # Configure the final block differently
    f = generate_subnet(final_bias, final_activation)
    g = generate_subnet(final_bias, final_activation)
    blocks.append(FullyReversibleBlock(f, g))

    revnet = FullyReversibleSequence(nn.ModuleList(blocks))
    return revnet

In [ ]:
# If revnet was previously assigned, delete them to free memory
try:
    del revnet
except Exception:
    pass

# Configure a RevNet
revnet = generate_revnet(8448//2, 1, 2, bias=True, activation=nn.ReLU)
# Train the RevNet
train(revnet, dataset, epochs=1, bs=256, lr=0.001, max_grad_norm=1000,
      verbose=True)
# Save the model
saveModel('/content/drive/MyDrive/csc412-models/revnet-10-2-e200-bs256-sigma01',
    revnet)

In [ ]:
def pr_to_binary_multitrack(pr, filename):
    """Converts a float-encoded pianoroll to a binary pianoroll
    
    Parameters
    ----------
    pr: torch.tensor
        An Nx128 dimensional tensor representing a pianoroll, with entries less
        than or equal to 0 correspending to silence, and entries greater than 0
        corresponding to a note being played.
    filename: str
        The name to be given to the generated multitrack.

    Returns
    -------
    multitrack: pypianoroll.Multitrack
        The generated Multitrack from the given pianoroll.
    """
    binary_pr = torch.where(pr <= 0, False, True).detach().numpy()
    tracks = [
        ppr.BinaryTrack(name='multitrack',
        program=1,
        is_drum=False,
        pianoroll=binary_pr)
    ]
    multitrack = ppr.Multitrack(
        name=filename,
        resolution=24,
        tracks=tracks)
    
    return multitrack

In [ ]:
def synthesize_samples(model, n, clip_band, filename, D_latent=8448,
                       tightness=0.1, padding=48, interleave_rate=1):
    """Generate new music samples from the model.
    
    Parameters
    ----------
    model: FullyReversibleSequence
        The model to be used for music generation.
    n: int
        The number of samples to be drawn.
    clip_band: [int]
        The minimum and maximum pitch that the input data has been clipped to,
        represented as an array of length 2.
    filename: str
        The filename to be used when naming Multitracks
    D_latent: int, optional
        The latent dimension of the model. This should be the same as the input
        dimension.
    tightness: float, optional
        The standard deviation to be used when sampling from high-dimensional
        fully-factored Gaussions (the laten space of the model).
    padding: int, optional
        The amount of silence inbetween generated samples. Represented in
        absolute timing (1/24th notes).
    interleave_rate: int, optional
        The rate at which samples should be interleaved with themself. A value
        > 1 will increase the length of each sample proportional to
        interleave_rate. A value of 1 will have no effect.

    Returns
    -------
    padded_pr: torch.tensor
        A pianoroll consisting of all generated tracks, concatenated together,
        with the specified amount of padding inbetween.
    """
    min_pitch, max_pitch = clip_band
    pitch_range = max_pitch - min_pitch + 1

    # Sample from the latent space, and reverse the model to create dataspace
    # samples.
    latent_samples = torch.randn(n, D_latent).to(device) * tightness
    clipped_samples = model.reverse(latent_samples).to(cpu)

    # Reshape the samples from linearized vectors to their appropriate
    # Nx128 pianoroll matrix format. Also reverse the pitch clipping by padding
    # the clipped samples with 0s.
    clipped_piano_rolls = clipped_samples.reshape(n, -1, pitch_range)
    clipped_piano_rolls = clipped_piano_rolls.repeat_interleave(interleave_rate, dim=1)
    bar_length = clipped_piano_rolls.size()[1]
    piano_rolls = torch.cat([
                             torch.zeros(n, bar_length, min_pitch),
                             clipped_piano_rolls,
                             torch.zeros(n, bar_length, 127-max_pitch)
                             ], dim=-1)

    pr_samples = []
    for i in range(len(piano_rolls)):
        pr_samples.append(piano_rolls[i])

        # Plot track
        sample_track = pr_to_binary_multitrack(piano_rolls[i], filename)
        fig, ax = plt.subplots(1, 1)
        fig.set_size_inches(16, 9)
        sample_track.plot(axs=[ax])

        # Add padding
        if i != len(piano_rolls)-1:
            pr_samples.append(torch.zeros(padding, 128))
    
    # Join all tracks together
    padded_pr = torch.cat(pr_samples)
    return padded_pr

In [ ]:
def get_input_samples(n, clip_band, filename, padding=48, interleave_rate=1):
    """Get random samples from the dataspace.
    
    Parameters
    ----------
    n: int
        The number of samples to be drawn.
    clip_band: [int]
        The minimum and maximum pitch that the input data has been clipped to,
        represented as an array of length 2.
    filename: str
        The filename to be used when naming Multitracks
    padding: int, optional
        The amount of silence inbetween generated samples. Represented in
        absolute timing (1/24th notes).
    interleave_rate: int, optional
        The rate at which samples should be interleaved with themself. A value
        > 1 will increase the length of each sample proportional to
        interleave_rate. A value of 1 will have no effect.

    Returns
    -------
    padded_pr: torch.tensor
        A pianoroll consisting of all sampled tracks, concatenated together,
        with the specified amount of padding inbetween.
    """
    min_pitch, max_pitch = clip_band
    pitch_range = max_pitch - min_pitch + 1

    # Reshape the samples from linearized vectors to their appropriate
    # Nx128 pianoroll matrix format. Also reverse the pitch clipping by padding
    # the clipped samples with 0s.
    clipped_samples = dataset[torch.randint(len(dataset), (n,))][0]
    clipped_piano_rolls = clipped_samples.reshape(n, -1, pitch_range)
    clipped_piano_rolls = clipped_piano_rolls.repeat_interleave(interleave_rate, dim=1)
    bar_length = clipped_piano_rolls.size()[1]
    piano_rolls = torch.cat([
                             torch.zeros(n, bar_length, min_pitch),
                             clipped_piano_rolls,
                             torch.zeros(n, bar_length, 127-max_pitch)
                             ], dim=-1)

    pr_samples = []
    for i in range(len(piano_rolls)):
        pr_samples.append(piano_rolls[i])

        # Plot track
        sample_track = pr_to_binary_multitrack(piano_rolls[i], '')
        fig, ax = plt.subplots(1, 1)
        fig.set_size_inches(16, 9)
        sample_track.plot(axs=[ax])

        # Add padding
        if i != len(piano_rolls)-1:
            pr_samples.append(torch.zeros(padding, 128))
    
    # Join all tracks together
    padded_pr = torch.cat(pr_samples)
    return padded_pr

In [ ]:
def to_waveform(pr):
    """Convert a pianoroll into an audio waveform, synthesized with FluidSynth.
    
    Parameters
    ----------
    pr: torch.tensor
        A pianoroll to be synthesized.

    Returns
    -------
    waveform: ndarray
        A synthesized waveform.
    """
    multitrack = pr_to_binary_multitrack(pr, '')
    pm = multitrack.to_pretty_midi()
    waveform = pm.fluidsynth()
    return waveform

In [ ]:
def save_audio(wave, filename):
    """Save a waveform as a .wav file.
    
    Parameters
    ----------
    wave: ndarray
        A synthesized waveform.

    filename: str
        The name to be given to the generated .wav file, saved to the /content
        directory on Colab.

    Returns
    -------
    None
    """
    scipy.io.wavfile.write('/content/{}.wav'.format(filename), 44100, wave)

In [ ]:
# Generate input samples
input_samples = get_input_samples(5, [20, 107], 'revnet-samples-sd-0-1')

In [ ]:
# Create an audio player to listen to the input samples.
Audio(to_waveform(input_samples),rate=44100)

In [ ]:
# Create samples of music from the revnet
rev_samples = synthesize_samples(revnet, 5, [20, 107], 'revnet-samples-sd-0-1', interleave_rate=2, tightness=.08)

In [ ]:
# Synthesize audio from the generated pianoroll samples
rev_audio = to_waveform(rev_samples)

In [ ]:
# Create an audio player to listen to the revnet samples.
Audio(rev_audio,rate=44100)

In [ ]:
# Save the generated audio samples
save_audio(track_audio, 'rev-sample')